In [1]:
import gensim
import pandas as pd
import numpy as np
from gensim.models import LdaModel, LsiModel
from sklearn.feature_extraction.text import TfidfVectorizer
import nltk

ModuleNotFoundError: No module named 'gensim'

In [2]:
df = pd.read_csv ('Sample.csv')
df

Full Text
0     @hamcore_ First the boss metal zone schematics...
1     @sippygup its in the vaccine and 5g makes it m...
2     Him and all the others that do Not like and ha...
3     @TimRunsHisMouth Him and all the others that d...
4     @NYGovCuomo 99.97% survival rate no vaccine fo...
...                                                 ...
9953  Waiting for the train and I hear two mfs say �...
9954  I played my radical left avant garde music and...
9955  You are such a fag @MayorKeller And what the F...
9956  .@seanspicer hahahaha Trump's accomplishments?...
9957  100%. It was about the election, not the virus...

[9958 rows x 1 columns]

In [3]:
%pylab inline

import pandas as pd
import pickle as pk
from scipy import sparse as sp

Populating the interactive namespace from numpy and matplotlib


In [4]:
p_df = pd.read_csv('Sample.csv')
docs = array(p_df['Full Text'])

In [5]:
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import RegexpTokenizer

def docs_preprocessor(docs):
    tokenizer = RegexpTokenizer(r'\w+')
    for idx in range(len(docs)):
        docs[idx] = docs[idx].lower()  # Convert to lowercase.
        docs[idx] = tokenizer.tokenize(docs[idx])  # Split into words.

    # Remove numbers, but not words that contain numbers.
    docs = [[token for token in doc if not token.isdigit()] for doc in docs]
    
    # Remove words that are only one character.
    docs = [[token for token in doc if len(token) > 3] for doc in docs]
    
    # Lemmatize all words in documents.
    lemmatizer = WordNetLemmatizer()
    docs = [[lemmatizer.lemmatize(token) for token in doc] for doc in docs]
  
    return docs

In [6]:
docs = docs_preprocessor(docs)

In [7]:
docs

[['hamcore_',
  'first',
  'bos',
  'metal',
  'zone',
  'schematic',
  'vaccine',
  'hitler',
  'stuff',
  'right',
  'cmon',
  'only',
  '42am'],
 ['sippygup', 'vaccine', 'make', 'more', 'powerful', 'watch'],
 ['others',
  'that',
  'like',
  'hate',
  'donaldtrump',
  'just',
  'because',
  'they',
  'part',
  'satanic',
  'deep',
  'state',
  'illuminati',
  'serf',
  'different',
  'same',
  'that',
  'gave',
  'power',
  'poisoning',
  'food',
  'water',
  'that',
  'monsanto',
  'plus',
  'behind',
  'vaccine',
  'withvp'],
 ['timrunshismouth',
  'others',
  'that',
  'like',
  'hate',
  'donaldtrump',
  'just',
  'because',
  'they',
  'part',
  'satanic',
  'deep',
  'state',
  'illuminati',
  'serf',
  'different',
  'same',
  'that',
  'gave',
  'power',
  'poisoning',
  'food',
  'water',
  'that',
  'monsanto',
  'plus',
  'behind',
  'vaccine',
  'withvp'],
 ['nygovcuomo', 'survival', 'rate', 'vaccine'],
 ['and_kell',
  'only',
  'coincidence',
  'extremely',
  'rare',
  

In [8]:
from gensim.models import Phrases
# Add bigrams and trigrams to docs (only ones that appear 10 times or more).
bigram = Phrases(docs, min_count=10)
trigram = Phrases(bigram[docs])

for idx in range(len(docs)):
    for token in bigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)
    for token in trigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)

In [9]:
from gensim.corpora import Dictionary

# Create a dictionary representation of the documents.
dictionary = Dictionary(docs)
print('Number of unique words in initital documents:', len(dictionary))

# Filter out words that occur less than 10 documents, or more than 20% of the documents.
dictionary.filter_extremes(no_below=4, no_above=0.40)
print('Number of unique words after removing rare and common words:', len(dictionary))

Number of unique words in initital documents: 20173
Number of unique words after removing rare and common words: 4673


In [10]:
corpus = [dictionary.doc2bow(doc) for doc in docs]


In [11]:
print('Number of unique tokens: %d' % len(dictionary))
print('Number of documents: %d' % len(corpus))

Number of unique tokens: 4673
Number of documents: 9958


In [12]:
from gensim.models import LdaModel


In [13]:
# Set training parameters.
num_topics = 50
chunksize = 1250 # size of the doc looked at every pass
passes = 7 # number of passes through documents
iterations = 2
eval_every = 1  # Don't evaluate model perplexity, takes too much time.

# Make a index to word dictionary.
temp = dictionary[0]  # This is only to "load" the dictionary.
id2word = dictionary.id2token

%time model = LdaModel(corpus=corpus, id2word=id2word, chunksize=chunksize, \
                       alpha='auto', eta='auto', \
                       iterations=iterations, num_topics=num_topics, \
                       passes=passes, eval_every=eval_every)

Wall time: 24.4 s


In [28]:
import pyLDAvis
pyLDAvis.enable_notebook()
import pyLDAvis.gensim_models
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning) 
#pcoa:Principal Coordinate Analysis(aka Classical Multidimensional Scaling)
pyLDAvis.gensim_models.prepare(model, corpus, dictionary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
16     0.072755  0.086562       1        1  4.768131
31    -0.004165  0.083753       2        1  4.405088
33    -0.205384 -0.002141       3        1  4.133024
43    -0.200684  0.093405       4        1  3.440149
37    -0.255953 -0.033270       5        1  3.406187
13     0.079133  0.245944       6        1  3.207282
23    -0.054111 -0.010649       7        1  3.147200
45    -0.144988 -0.063824       8        1  3.070585
12     0.150139  0.073987       9        1  3.005695
18    -0.151292  0.007763      10        1  2.785403
30    -0.024247  0.066840      11        1  2.440284
41    -0.008882  0.167168      12        1  2.322721
1     -0.177229 -0.068691      13        1  2.264795
15    -0.001754 -0.010016      14        1  2.174040
48     0.108401  0.237235      15        1  2.118317
9     -0.017609  0.000181      16        1  1.999970
2     -0.065567  0.072063      17        1  1.954223
27    -0.041261  0.003222      18        1  1.912580
10    -0.062993 -0.061344      19        1  1.873206
40    -0.103200 -0.033938      20        1  1.830838
4     -0.007767 -0.020691      21        1  1.798124
22     0.057515  0.077713      22        1  1.735295
24     0.045639 -0.021376      23        1  1.726399
20     0.101177 -0.066586      24        1  1.724213
38    -0.057939 -0.080017      25        1  1.697846
0     -0.027633 -0.021751      26        1  1.696995
49    -0.098716  0.002407      27        1  1.688253
47    -0.062383 -0.053877      28        1  1.683226
46    -0.092338  0.041774      29        1  1.682595
29     0.035830  0.031815      30        1  1.674448
35     0.008925  0.049806      31        1  1.654398
25     0.009533 -0.111638      32        1  1.648012
42     0.087117 -0.047580      33        1  1.570126
19    -0.000199 -0.004188      34        1  1.547419
11     0.081968 -0.015038      35        1  1.487880
7     -0.004196 -0.096764      36        1  1.450153
8      0.055108 -0.023034      37        1  1.423401
6      0.024222 -0.041915      38        1  1.413197
36     0.059195  0.053871      39        1  1.345858
32     0.119562 -0.003911      40        1  1.320819
26     0.029912  0.083213      41        1  1.312518
21     0.041101 -0.036119      42        1  1.310611
3     -0.033892 -0.062996      43        1  1.277653
28     0.048596  0.012558      44        1  1.265520
34     0.123890 -0.041418      45        1  1.259634
14    -0.004730  0.009801      46        1  1.256439
17     0.174952 -0.120186      47        1  1.129012
44     0.075649 -0.094812      48        1  1.086841
39     0.169590 -0.131397      49        1  1.015940
5      0.149204 -0.121916      50        1  0.857458, topic_info=              Term         Freq        Total Category  logprob  loglift
17      deep_state  3707.000000  3707.000000  Default  30.0000  30.0000
71    cause_autism  1988.000000  1988.000000  Default  29.0000  29.0000
77            have  2010.000000  2010.000000  Default  28.0000  28.0000
121           will  2034.000000  2034.000000  Default  27.0000  27.0000
35           state  1377.000000  1377.000000  Default  26.0000  26.0000
...            ...          ...          ...      ...      ...      ...
924         voting    16.226489    17.311805  Topic50  -4.5775   4.6942
1281          hour    16.007527    17.092843  Topic50  -4.5911   4.6934
2540        posted    15.563293    16.648608  Topic50  -4.6193   4.6915
2020       promote    12.138353    13.223669  Topic50  -4.8678   4.6733
424           than    21.175300   345.553401  Topic50  -4.3113   1.9666

[1868 rows x 6 columns], token_table=      Topic      Freq           Term
term                                
2659     35  0.933352        ability
1235     37  0.982938           able
2672     24  0.579034        aborted
2672     30  0.405323        aborted
2673     30  0.962042  aborted_fetal
...     ...       ...            ...
818

In [29]:
import pyLDAvis
pyLDAvis.enable_notebook()
import pyLDAvis.gensim_models
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning) 
# mmds:Metric Multidimensional Scaling
pyLDAvis.gensim_models.prepare(model, corpus, dictionary, mds='mmds')

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
16     0.238658  0.488643       1        1  4.767669
31     0.429777  0.229843       2        1  4.405066
33    -0.089238  0.285337       3        1  4.132123
43     0.024428  0.195874       4        1  3.441054
37     0.134325  0.099750       5        1  3.405271
13     0.495037  0.008936       6        1  3.207639
23     0.032942  0.398377       7        1  3.146960
45    -0.439645 -0.137955       8        1  3.070964
12    -0.379872  0.374281       9        1  3.005453
18     0.183321  0.203826      10        1  2.786008
30     0.330450  0.273888      11        1  2.439423
41    -0.072077  0.449632      12        1  2.322594
1     -0.132569  0.139880      13        1  2.265183
15    -0.181953  0.454594      14        1  2.174080
48    -0.068813 -0.235701      15        1  2.117949
9     -0.239742  0.368769      16        1  2.000050
2     -0.010712  0.081136      17        1  1.953682
27    -0.403475  0.056710      18        1  1.912787
10     0.144927  0.360048      19        1  1.873626
40     0.329249  0.101055      20        1  1.831004
4     -0.260536  0.082933      21        1  1.798428
22     0.159800 -0.447328      22        1  1.735058
24     0.316485  0.367527      23        1  1.726322
20    -0.382700 -0.359511      24        1  1.724364
38    -0.148206 -0.127012      25        1  1.697374
0      0.098966 -0.056713      26        1  1.696623
49     0.285025 -0.016022      27        1  1.689120
47    -0.251925 -0.130891      28        1  1.683415
46     0.218516 -0.115990      29        1  1.682535
29    -0.101067 -0.379697      30        1  1.674282
35    -0.382569 -0.229376      31        1  1.653920
25     0.202270 -0.325738      32        1  1.648425
42    -0.515473 -0.043408      33        1  1.570189
19     0.345618 -0.212776      34        1  1.546995
11     0.459910 -0.203174      35        1  1.488093
7      0.449982 -0.089712      36        1  1.450405
8      0.471902  0.119440      37        1  1.423736
6      0.266489 -0.372780      38        1  1.413259
36    -0.208622 -0.396307      39        1  1.346200
32    -0.123105 -0.497758      40        1  1.320852
26    -0.345617 -0.047287      41        1  1.313021
21    -0.414024  0.154079      42        1  1.310848
3      0.086470 -0.219257      43        1  1.277200
28     0.038711 -0.398581      44        1  1.265569
34     0.066020  0.516576      45        1  1.259672
14    -0.282501  0.246458      46        1  1.256406
17    -0.484999  0.220504      47        1  1.128280
44    -0.292657 -0.348133      48        1  1.086865
39     0.033413 -0.523257      49        1  1.016486
5      0.369401 -0.363735      50        1  0.857475, topic_info=              Term         Freq        Total Category  logprob  loglift
17      deep_state  3707.000000  3707.000000  Default  30.0000  30.0000
71    cause_autism  1989.000000  1989.000000  Default  29.0000  29.0000
77            have  2010.000000  2010.000000  Default  28.0000  28.0000
121           will  2034.000000  2034.000000  Default  27.0000  27.0000
35           state  1377.000000  1377.000000  Default  26.0000  26.0000
...            ...          ...          ...      ...      ...      ...
924         voting    16.226794    17.312128  Topic50  -4.5775   4.6942
1281          hour    16.007828    17.093162  Topic50  -4.5911   4.6933
2540        posted    15.563585    16.648919  Topic50  -4.6193   4.6915
2020       promote    12.138581    13.223915  Topic50  -4.8678   4.6733
424           than    21.175698   345.615142  Topic50  -4.3113   1.9665

[1868 rows x 6 columns], token_table=      Topic      Freq           Term
term                                
2659     35  0.933225        ability
1235     37  0.982709           able
2672     24  0.579027        aborted
2672     30  0.405319        aborted
2673     30  0.962135  aborted_fetal
...     ...       ...            ...
818

In [33]:
import pyLDAvis
pyLDAvis.enable_notebook()
import pyLDAvis.gensim_models
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning) 
#tsne:t-distributed Stochastic Neighbor Embedding
pyLDAvis.gensim_models.prepare(model, corpus, dictionary, mds='tsne')

C:\Users\Wahbeh\anaconda3\lib\site-packages\sklearn\manifold\_t_sne.py:691: FutureWarning: 'square_distances' has been introduced in 0.24 to help phase out legacy squaring behavior. The 'legacy' setting will be removed in 1.1 (renaming of 0.26), and the default setting will be changed to True. In 1.3, 'square_distances' will be removed altogether, and distances will be squared by default. Set 'square_distances'=True to silence this warning.
  warnings.warn(


PreparedData(topic_coordinates=                x          y  topics  cluster      Freq
topic                                                  
16     -66.677643  33.792923       1        1  4.768605
31     -42.446949  47.413105       2        1  4.405653
33     -15.518475  16.047625       3        1  4.131352
43      24.575277   2.399667       4        1  3.441018
37      -5.986637   4.288529       5        1  3.405162
13      75.455711 -17.305550       6        1  3.207714
23     -48.066113 -29.859911       7        1  3.146886
45     -37.914398  15.639928       8        1  3.070441
12      31.627901  83.887726       9        1  3.006400
18       5.353085 -17.582071      10        1  2.786848
30      13.065767 -58.837173      11        1  2.439930
41      27.455349 -69.248276      12        1  2.322283
1       -8.747060 -11.533638      13        1  2.264782
15      60.347553  16.360476      14        1  2.174178
48      58.899582 -20.971834      15        1  2.117780
9      -24.039534  33.839859      16        1  2.000178
2       37.309059  13.999663      17        1  1.953922
27       9.667380 -38.100739      18        1  1.912608
10     -25.221266 -38.895287      19        1  1.873776
40       0.892199  20.001112      20        1  1.831059
4       43.573044  34.378193      21        1  1.798264
22      45.119362  -3.112282      22        1  1.734357
24      38.592587  57.068493      23        1  1.726464
20     137.861893  43.143108      24        1  1.724314
38      -7.504665 -29.052820      25        1  1.697412
0       -2.565194  39.018742      26        1  1.697028
49       9.371823   6.666193      27        1  1.688020
47      -6.583941 -47.336494      28        1  1.683587
46      15.155695  -7.762383      29        1  1.682583
29      69.915878  41.549328      30        1  1.674470
35      10.485427  57.837433      31        1  1.654368
25      19.481239  22.140942      32        1  1.648745
42      85.338753   7.761809      33        1  1.570019
19      21.376337 -26.835926      34        1  1.546989
11     -17.366182  64.224907      35        1  1.487928
7      -16.514378 -67.020203      36        1  1.450113
8      -44.464985 -51.033092      37        1  1.423412
6       20.605635  36.597054      38        1  1.413201
36     -61.866623   0.546633      39        1  1.345788
32     118.497246 -53.282040      40        1  1.320761
26      39.185432 -19.809603      41        1  1.312803
21      31.743587 -42.885338      42        1  1.310479
3      -23.740076 -19.254072      43        1  1.277390
28     -41.451092  -9.614955      44        1  1.265690
34      25.443060 -11.579443      45        1  1.259659
14     -21.593277  -0.562450      46        1  1.256358
17      61.854900 -75.229584      47        1  1.128673
44       2.582088  -4.885757      48        1  1.086890
39      68.256042 -63.283485      49        1  1.016271
5       53.575199 -44.079895      50        1  0.857391, topic_info=              Term         Freq        Total Category  logprob  loglift
17      deep_state  3708.000000  3708.000000  Default  30.0000  30.0000
71    cause_autism  1988.000000  1988.000000  Default  29.0000  29.0000
77            have  2011.000000  2011.000000  Default  28.0000  28.0000
121           will  2034.000000  2034.000000  Default  27.0000  27.0000
35           state  1377.000000  1377.000000  Default  26.0000  26.0000
...            ...          ...          ...      ...      ...      ...
924         voting    16.225211    17.310525  Topic50  -4.5775   4.6943
1281          hour    16.006266    17.091581  Topic50  -4.5911   4.6934
2540        posted    15.562066    16.647381  Topic50  -4.6193   4.6916
2020       promote    12.137396    13.222711  Topic50  -4.8678   4.6734
424           than    21.173632   345.654971  Topic50  -4.3113   1.9663

[1868 rows x 6 columns], token_table=      Topic      Freq           Term
term                                
2659     35  0.933324        ability
1235     37  0.982931           

In [34]:
# use the lda model to transform documents
lda_docs = model[corpus]
for row in lda_docs:
    print (row)

[(1, 0.014012306), (2, 0.01215913), (4, 0.010329183), (9, 0.055370543), (10, 0.010490349), (12, 0.05753991), (13, 0.016356513), (15, 0.012375164), (18, 0.016175082), (23, 0.01743575), (25, 0.09552223), (26, 0.13863441), (27, 0.011643506), (30, 0.015111866), (31, 0.01495045), (33, 0.064879104), (37, 0.061092086), (40, 0.010418069), (41, 0.012126504), (43, 0.06289128), (44, 0.049073126), (45, 0.011588843), (46, 0.010738945), (47, 0.010024187), (48, 0.010536989), (49, 0.010838166)]
[(0, 0.013725924), (1, 0.020087788), (2, 0.017431108), (3, 0.011714619), (4, 0.01480773), (6, 0.010760093), (7, 0.07408455), (8, 0.011805523), (9, 0.017548172), (10, 0.015024852), (11, 0.13605557), (12, 0.02055341), (13, 0.023448402), (14, 0.0115333), (15, 0.01774081), (16, 0.010594053), (18, 0.023130473), (19, 0.011022262), (20, 0.01360429), (21, 0.010735642), (22, 0.013527838), (23, 0.024995578), (24, 0.013984051), (25, 0.075021476), (26, 0.011625317), (27, 0.01669192), (28, 0.011132922), (30, 0.02166404), (3

[(1, 0.14012255), (11, 0.035800282), (13, 0.011661971), (18, 0.07528781), (23, 0.011839996), (25, 0.03545796), (28, 0.035291217), (30, 0.010295236), (31, 0.010204982), (33, 0.057180803), (37, 0.05732175), (41, 0.13288757), (42, 0.035499137), (43, 0.021290883), (46, 0.04557229), (47, 0.03701849), (48, 0.044192396)]
[(1, 0.01000314), (3, 0.035557084), (9, 0.08484892), (11, 0.06806907), (12, 0.0105758635), (13, 0.015597521), (18, 0.012159454), (23, 0.012349285), (27, 0.046432238), (28, 0.035477646), (30, 0.03750378), (31, 0.010385722), (32, 0.035832256), (33, 0.08608447), (35, 0.037549715), (37, 0.017969439), (42, 0.0649608), (43, 0.026140543), (44, 0.033516943), (48, 0.13439149)]
[(1, 0.013303066), (2, 0.011615033), (9, 0.052780885), (10, 0.0530503), (12, 0.053985473), (13, 0.015082042), (15, 0.052871358), (18, 0.015321757), (20, 0.04767936), (23, 0.09916723), (27, 0.010752391), (30, 0.013968218), (31, 0.013825879), (33, 0.10431202), (34, 0.045684468), (37, 0.02360655), (41, 0.011273304)

[(0, 0.03656257), (4, 0.037468355), (6, 0.062976085), (8, 0.03378017), (10, 0.034436174), (13, 0.010475193), (14, 0.03292939), (15, 0.038089246), (18, 0.010345187), (23, 0.058526747), (27, 0.03513994), (33, 0.061083153), (36, 0.032605477), (37, 0.012536938), (38, 0.034416594), (40, 0.0347579), (42, 0.14384419), (43, 0.012842042), (45, 0.03564953), (46, 0.034802705), (48, 0.034582913)]
[(1, 0.05790721), (2, 0.043158174), (5, 0.03493126), (7, 0.038062412), (9, 0.04048563), (10, 0.04200383), (12, 0.04138058), (13, 0.042942047), (18, 0.0118411165), (23, 0.04272719), (27, 0.04047913), (30, 0.010899579), (31, 0.010779982), (33, 0.018041782), (37, 0.07893982), (40, 0.15190808), (43, 0.015227445), (46, 0.043405827), (49, 0.0431714)]
[(1, 0.039256234), (3, 0.032835435), (4, 0.034225114), (8, 0.07001507), (9, 0.03634468), (11, 0.032327462), (12, 0.035215415), (13, 0.010209432), (18, 0.010228177), (21, 0.032899067), (22, 0.117277004), (23, 0.011240593), (30, 0.028289609), (31, 0.06717969), (33, 0

[(1, 0.016085587), (2, 0.058302928), (4, 0.010327293), (9, 0.055471472), (10, 0.010496592), (11, 0.051654898), (12, 0.014334478), (13, 0.01635352), (15, 0.012372899), (18, 0.026691513), (23, 0.017432561), (27, 0.011641376), (30, 0.01510906), (31, 0.015028838), (32, 0.051540904), (33, 0.06486109), (36, 0.050864484), (37, 0.018658856), (39, 0.11855637), (40, 0.05364431), (41, 0.012121233), (43, 0.019772088), (45, 0.011586722), (46, 0.010736865), (47, 0.010022353), (48, 0.053696454), (49, 0.010836182)]
[(0, 0.029021664), (1, 0.033056773), (6, 0.02794207), (7, 0.060475532), (10, 0.06975747), (15, 0.035211902), (19, 0.07929402), (20, 0.026801448), (21, 0.054304224), (25, 0.028847668), (29, 0.12350162), (30, 0.057085413), (33, 0.01189213), (35, 0.012530105), (37, 0.051214375), (40, 0.029447934), (42, 0.028623868), (43, 0.06290337)]
[(0, 0.088259846), (1, 0.014240935), (2, 0.010702544), (9, 0.010756198), (12, 0.013475297), (13, 0.07807784), (15, 0.010639383), (18, 0.08572495), (23, 0.01544554

[(1, 0.010109786), (6, 0.036832117), (8, 0.03795659), (9, 0.041367542), (12, 0.01032021), (13, 0.011773297), (14, 0.037148762), (15, 0.040819563), (18, 0.011816892), (23, 0.15824774), (25, 0.03969717), (30, 0.012393017), (31, 0.16919707), (33, 0.07871167), (37, 0.01364775), (41, 0.03589482), (43, 0.014463497), (47, 0.0394491)]
[(13, 0.49995798), (18, 0.012584538), (22, 0.012271833), (23, 0.010062822), (24, 0.018421931), (31, 0.11615458), (32, 0.039500944), (33, 0.012503346), (35, 0.018787606), (37, 0.010795177), (40, 0.031339753), (43, 0.012925941)]
[(0, 0.01106575), (1, 0.01610605), (2, 0.014379479), (4, 0.011873642), (9, 0.014070498), (10, 0.06248279), (12, 0.016472736), (13, 0.020310298), (15, 0.01423756), (18, 0.054299593), (20, 0.010903294), (22, 0.010863762), (23, 0.02012652), (24, 0.011217243), (25, 0.010446995), (27, 0.013386246), (30, 0.018059345), (31, 0.017189981), (33, 0.02498866), (37, 0.021483041), (38, 0.011316783), (40, 0.012068316), (41, 0.06040196), (43, 0.08260321), 

...

[(0, 0.05196471), (4, 0.03374498), (5, 0.036214463), (7, 0.032486863), (8, 0.033521634), (12, 0.03585083), (13, 0.010648199), (18, 0.010400568), (23, 0.05257491), (25, 0.025204541), (31, 0.15733029), (33, 0.013612865), (34, 0.03098107), (36, 0.032102384), (37, 0.04239474), (41, 0.12199886), (43, 0.049685415), (48, 0.038738783)]
[(3, 0.079674676), (6, 0.03353764), (9, 0.038466997), (11, 0.034222357), (13, 0.010768511), (18, 0.01070458), (22, 0.035882708), (23, 0.08869602), (26, 0.06325121), (29, 0.032968868), (30, 0.069171146), (33, 0.014256452), (37, 0.012671454), (42, 0.033971824), (43, 0.01350151), (44, 0.032441113), (47, 0.06947378), (48, 0.062961), (49, 0.06634868)]
[(1, 0.03564561), (2, 0.034470852), (4, 0.1951425), (13, 0.037118778), (18, 0.010053624), (22, 0.03280771), (23, 0.010860064), (27, 0.0608575), (31, 0.14402488), (33, 0.04040978), (36, 0.031684108), (37, 0.011624017), (38, 0.14073877), (43, 0.012317534)]
[(0, 0.012160844), (1, 0.012188304), (2, 0.0104003), (12, 0.035398

[(0, 0.028353672), (2, 0.031036649), (10, 0.029448377), (12, 0.03324404), (13, 0.04285821), (19, 0.09218991), (22, 0.020399462), (24, 0.02801681), (25, 0.010985095), (27, 0.030229077), (28, 0.030309582), (30, 0.031423684), (33, 0.06758181), (37, 0.0389067), (41, 0.032122917), (42, 0.17193058), (43, 0.039979853), (46, 0.031057192), (48, 0.030920736), (49, 0.029453931)]
[(4, 0.031155067), (13, 0.03877622), (18, 0.020562196), (23, 0.036556676), (25, 0.03170883), (27, 0.1183471), (29, 0.029726136), (33, 0.014636485), (34, 0.028745184), (35, 0.088789694), (36, 0.043182824), (37, 0.0117134), (43, 0.09166365), (44, 0.029840427), (45, 0.03507408), (47, 0.03221365), (48, 0.12882517)]
[(4, 0.031143818), (13, 0.03859739), (18, 0.021235686), (23, 0.036486648), (25, 0.031636454), (27, 0.117845096), (29, 0.029683128), (33, 0.014685033), (34, 0.028736832), (35, 0.08798765), (36, 0.042329427), (37, 0.011567809), (43, 0.093237825), (44, 0.029795295), (45, 0.034893353), (47, 0.032136258), (48, 0.1297382

[(0, 0.011574745), (1, 0.016937677), (2, 0.01469761), (4, 0.012485623), (7, 0.010197788), (9, 0.014796316), (10, 0.012668696), (11, 0.01019131), (12, 0.017330281), (13, 0.01977129), (15, 0.014958746), (18, 0.019503215), (20, 0.011470903), (22, 0.011406439), (23, 0.021075841), (24, 0.011791111), (25, 0.01098794), (27, 0.0140743395), (30, 0.018266745), (31, 0.32012475), (32, 0.010043529), (33, 0.038808607), (37, 0.022558425), (38, 0.011903257), (40, 0.012600063), (41, 0.014654484), (42, 0.010106603), (43, 0.023904312), (45, 0.014008264), (46, 0.012980794), (47, 0.012116953), (48, 0.06387729), (49, 0.013100866)]
[(1, 0.013517964), (2, 0.011190069), (9, 0.011480969), (10, 0.05664513), (12, 0.01319353), (13, 0.054964304), (15, 0.05117846), (18, 0.014994544), (22, 0.17750046), (23, 0.016820055), (27, 0.011121712), (30, 0.060935453), (31, 0.013771408), (33, 0.10031301), (34, 0.045727987), (37, 0.01765849), (38, 0.05306017), (41, 0.011156447), (43, 0.025199544), (45, 0.010664481), (49, 0.01002

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[(16, 0.81436145), (33, 0.011891653)]
[(16, 0.8141916), (33, 0.012437066)]
[(1, 0.04332116), (9, 0.042038094), (12, 0.010009716), (13, 0.011418375), (18, 0.011484929), (19, 0.15653455), (21, 0.036625076), (23, 0.028543709), (27, 0.06861015), (30, 0.04261432), (31, 0.010480472), (33, 0.015123127), (34, 0.034572594), (37, 0.013988858), (38, 0.1546899), (41, 0.039272513), (43, 0.014599856), (44, 0.034500316), (49, 0.039497834)]
[(4, 0.036753234), (8, 0.06611057), (10, 0.050691187), (11, 0.03681664), (12, 0.010009786), (13, 0.101821564), (16, 0.03525661), (17, 0.03351501), (18, 0.011327388), (22, 0.036775164), (23, 0.012173182), (26, 0.03581182), (30, 0.010552118), (31, 0.1652172), (33, 0.016544843), (34, 0.038125567), (37, 0.016564768), (42, 0.036029194), (43, 0.015575012), (47, 0.037686396)]
[(1, 0.012453533), (5, 0.04691566), (11, 0.039634272), (12, 0.011004942), (13, 0.012683389), (15, 0.042629696), (18, 0.027496727), (22, 0.021694826), (23, 0.013454768), (24, 0.04066515), (25, 0.0308

In [35]:
# extract the scores and round them to 3 decimal places
#scores = np.round([[doc[1] for doc in row] for row in lda_docs], 3)
scores = [[doc[1] for doc in row] for row in lda_docs]
scores

[[0.014012305,
  0.012159129,
  0.010329182,
  0.05537486,
  0.010490008,
  0.057539925,
  0.016356511,
  0.012375162,
  0.01617958,
  0.01743575,
  0.0955222,
  0.13866548,
  0.011643505,
  0.0151118655,
  0.014951414,
  0.064879104,
  0.061040133,
  0.010418068,
  0.012126654,
  0.06289139,
  0.049073122,
  0.011588842,
  0.010738948,
  0.010024186,
  0.010536988,
  0.010838165],
 [0.013725924,
  0.020087788,
  0.017431108,
  0.011714619,
  0.01480773,
  0.010760093,
  0.07408455,
  0.011805523,
  0.017548172,
  0.015024852,
  0.13605557,
  0.02055341,
  0.023448402,
  0.0115333,
  0.01774081,
  0.010594053,
  0.023130473,
  0.011022262,
  0.01360429,
  0.010735642,
  0.013527838,
  0.024995578,
  0.013984051,
  0.075021476,
  0.011625317,
  0.01669192,
  0.011132922,
  0.02166404,
  0.021408055,
  0.01191145,
  0.031022178,
  0.01177924,
  0.010939209,
  0.026753895,
  0.014117054,
  0.014935155,
  0.017379962,
  0.011986254,
  0.028350096,
  0.016613556,
  0.015394993,
  0.01437049

In [37]:
# convert the documents scores into a data frame
df_lda = pd.DataFrame(scores, columns=["topic 1", "topic 2", "topic 3", "topic 4", "topic 5", "topic 6", "topic 7", "topic 8", "topic 9", "topic 10", "topic 11", "topic 12", "topic 13", "topic 14", "topic 15", "topic 16", "topic 17", "topic 18", "topic 19", "topic 20", "topic 21", "topic 22", "topic 23", "topic 24", "topic 25", "topic 26", "topic 27", "topic 28", "topic 29", "topic 30", "topic 31", "topic 32", "topic 33", "topic 34", "topic 35", "topic 36", "topic 37", "topic 38", "topic 39", "topic 40", "topic 41", "topic 42", "topic 43", "topic 44", "topic 45", "topic 46", "topic 47", "topic 48", "topic 49"])
df_lda

topic 1   topic 2   topic 3   topic 4   topic 5   topic 6   topic 7  \
0     0.014012  0.012159  0.010329  0.055375  0.010490  0.057540  0.016357   
1     0.013726  0.020088  0.017431  0.011715  0.014808  0.010760  0.074085   
2     0.014903  0.011054  0.027970  0.034616  0.033751  0.011028  0.086728   
3     0.012614  0.011927  0.027293  0.033671  0.032937  0.010432  0.033412   
4     0.012212  0.017872  0.015508  0.010422  0.013174  0.010760  0.010503   
...        ...       ...       ...       ...       ...       ...       ...   
9953  0.010047  0.015544  0.013192  0.010923  0.012926  0.011242  0.191830   
9954  0.052058  0.013901  0.011869  0.046494  0.049407  0.011809  0.056839   
9955  0.012385  0.044423  0.041316  0.045741  0.012990  0.106525  0.013683   
9956  0.033958  0.035876  0.037449  0.027242  0.011199  0.045389  0.087763   
9957  0.018173  0.010784  0.015264  0.010992  0.012689  0.054926  0.047158   

       topic 8   topic 9  topic 10  ...  topic 40  topic 41  topic 42  \
0     0.012375  0.016180  0.017436  ...       NaN       NaN       NaN   
1     0.011806  0.017548  0.015025  ...  0.016614  0.015395   0.01437   
2     0.034911  0.031155  0.037293  ...       NaN       NaN       NaN   
3     0.084426  0.034373  0.030313  ...       NaN       NaN       NaN   
4     0.015613  0.013368  0.065891  ...       NaN       NaN       NaN   
...        ...       ...       ...  ...       ...       ...       ...   
9953  0.060223  0.017104  0.012965  ...       NaN       NaN       NaN   
9954  0.013743  0.056235  0.011875  ...       NaN       NaN       NaN   
9955  0.049279  0.042556  0.041522  ...       NaN       NaN       NaN   
9956  0.011610  0.035705  0.040032  ...       NaN       NaN       NaN   
9957  0.025834  0.044719  0.020679  ...       NaN       NaN       NaN   

      topic 43  topic 44  topic 45  topic 46  topic 47  topic 48  topic 49  
0          NaN       NaN       NaN       NaN       NaN       NaN       NaN  
1     0.015106  0.015537       NaN       NaN       NaN       NaN       NaN  
2          NaN       NaN       NaN       NaN       NaN       NaN       NaN  
3          NaN       NaN       NaN       NaN       NaN       NaN       NaN  
4          NaN       NaN       NaN       NaN       NaN       NaN       NaN  
...        ...       ...       ...       ...       ...       ...       ...  
9953       NaN       NaN       NaN       NaN       NaN       NaN       NaN  
9954       NaN       NaN       NaN       NaN       NaN       NaN       NaN  
9955       NaN       NaN       NaN       NaN       NaN       NaN       NaN  
9956       NaN       NaN       NaN       NaN       NaN       NaN       NaN  
9957       NaN       NaN       NaN       NaN       NaN       NaN       NaN  

[9958 rows x 49 columns]

In [38]:
df_lda=df_lda.fillna(0)
df_lda

topic 1   topic 2   topic 3   topic 4   topic 5   topic 6   topic 7  \
0     0.014012  0.012159  0.010329  0.055375  0.010490  0.057540  0.016357   
1     0.013726  0.020088  0.017431  0.011715  0.014808  0.010760  0.074085   
2     0.014903  0.011054  0.027970  0.034616  0.033751  0.011028  0.086728   
3     0.012614  0.011927  0.027293  0.033671  0.032937  0.010432  0.033412   
4     0.012212  0.017872  0.015508  0.010422  0.013174  0.010760  0.010503   
...        ...       ...       ...       ...       ...       ...       ...   
9953  0.010047  0.015544  0.013192  0.010923  0.012926  0.011242  0.191830   
9954  0.052058  0.013901  0.011869  0.046494  0.049407  0.011809  0.056839   
9955  0.012385  0.044423  0.041316  0.045741  0.012990  0.106525  0.013683   
9956  0.033958  0.035876  0.037449  0.027242  0.011199  0.045389  0.087763   
9957  0.018173  0.010784  0.015264  0.010992  0.012689  0.054926  0.047158   

       topic 8   topic 9  topic 10  ...  topic 40  topic 41  topic 42  \
0     0.012375  0.016180  0.017436  ...  0.000000  0.000000   0.00000   
1     0.011806  0.017548  0.015025  ...  0.016614  0.015395   0.01437   
2     0.034911  0.031155  0.037293  ...  0.000000  0.000000   0.00000   
3     0.084426  0.034373  0.030313  ...  0.000000  0.000000   0.00000   
4     0.015613  0.013368  0.065891  ...  0.000000  0.000000   0.00000   
...        ...       ...       ...  ...       ...       ...       ...   
9953  0.060223  0.017104  0.012965  ...  0.000000  0.000000   0.00000   
9954  0.013743  0.056235  0.011875  ...  0.000000  0.000000   0.00000   
9955  0.049279  0.042556  0.041522  ...  0.000000  0.000000   0.00000   
9956  0.011610  0.035705  0.040032  ...  0.000000  0.000000   0.00000   
9957  0.025834  0.044719  0.020679  ...  0.000000  0.000000   0.00000   

      topic 43  topic 44  topic 45  topic 46  topic 47  topic 48  topic 49  
0     0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  
1     0.015106  0.015537       0.0       0.0       0.0       0.0       0.0  
2     0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  
3     0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  
4     0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  
...        ...       ...       ...       ...       ...       ...       ...  
9953  0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  
9954  0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  
9955  0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  
9956  0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  
9957  0.000000  0.000000       0.0       0.0       0.0       0.0       0.0  

[9958 rows x 49 columns]

In [39]:
from __future__ import print_function
import time
import numpy as np
import pandas as pd
#from sklearn.datasets import fetch_mldata
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
%matplotlib inline
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import seaborn as sns

In [40]:
N = 9958
rndperm = np.random.permutation(df_lda.shape[0])
df_subset = df_lda.loc[rndperm[:N],:].copy()
#data_subset = df_subset[feat_cols].values
data_subset = df_subset.values
pca = PCA(n_components=3)
pca_result = pca.fit_transform(data_subset)
df_subset['pca-one'] = pca_result[:,0]
df_subset['pca-two'] = pca_result[:,1] 
df_subset['pca-three'] = pca_result[:,2]
print('Explained variation per principal component: {}'.format(pca.explained_variance_ratio_))

Explained variation per principal component: [0.22358522 0.07670717 0.06275405]


In [41]:
df_subset

topic 1   topic 2   topic 3   topic 4   topic 5   topic 6   topic 7  \
4744  0.015838  0.012530  0.010396  0.012793  0.010703  0.014338  0.016384   
737   0.067018  0.070210  0.097141  0.036558  0.013584  0.038779  0.011044   
41    0.011574  0.125247  0.066998  0.012500  0.010198  0.014820  0.012669   
6832  0.178995  0.083377  0.011742  0.010045  0.012288  0.010506  0.044998   
8242  0.034919  0.100883  0.028214  0.026348  0.072473  0.029042  0.052508   
...        ...       ...       ...       ...       ...       ...       ...   
2359  0.020305  0.062828  0.010459  0.012938  0.012420  0.100938  0.016446   
8584  0.015668  0.022931  0.019898  0.013373  0.016903  0.012283  0.013806   
7458  0.044860  0.034797  0.039477  0.010212  0.031608  0.010175  0.058290   
9514  0.013726  0.020088  0.017431  0.011715  0.014808  0.010760  0.012094   
6453  0.012001  0.010365  0.044050  0.010445  0.224639  0.012221  0.013942   

       topic 8   topic 9  topic 10  ...  topic 43  topic 44  topic 45  \
4744  0.012603  0.017097  0.051422  ...  0.000000  0.000000  0.000000   
737   0.035768  0.011860  0.039330  ...  0.000000  0.000000  0.000000   
41    0.010195  0.017331  0.019772  ...  0.000000  0.000000  0.000000   
6832  0.013947  0.036329  0.036766  ...  0.000000  0.000000  0.000000   
8242  0.029455  0.029372  0.135245  ...  0.000000  0.000000  0.000000   
...        ...       ...       ...  ...       ...       ...       ...   
2359  0.012529  0.018596  0.018995  ...  0.000000  0.000000  0.000000   
8584  0.013476  0.020032  0.017151  ...  0.017574  0.016404  0.017243   
7458  0.140811  0.033067  0.014760  ...  0.000000  0.000000  0.000000   
9514  0.011805  0.017548  0.015025  ...  0.015106  0.015537  0.000000   
6453  0.043729  0.010549  0.013753  ...  0.000000  0.000000  0.000000   

      topic 46  topic 47  topic 48  topic 49   pca-one   pca-two  pca-three  
4744  0.000000       0.0       0.0       0.0 -0.026899 -0.091953   0.022215  
737   0.000000       0.0       0.0       0.0  0.020286  0.070736   0.007153  
41    0.000000       0.0       0.0       0.0 -0.028731 -0.052142   0.073896  
6832  0.000000       0.0       0.0       0.0  0.135944  0.012176  -0.039023  
8242  0.000000       0.0       0.0       0.0 -0.011364  0.046301  -0.045453  
...        ...       ...       ...       ...       ...       ...        ...  
2359  0.000000       0.0       0.0       0.0 -0.021833 -0.012689  -0.038967  
8584  0.017736       0.0       0.0       0.0 -0.019984 -0.092339   0.051536  
7458  0.000000       0.0       0.0       0.0 -0.001639  0.066817  -0.043903  
9514  0.000000       0.0       0.0       0.0 -0.028873 -0.089865   0.015798  
6453  0.000000       0.0       0.0       0.0 -0.032934  0.001054   0.002705  

[9958 rows x 52 columns]

In [42]:
from sklearn.manifold import TSNE
tsne_model = TSNE(n_components=2, verbose=1, random_state=2, angle=.70, init='pca')
# 13-D -> 2-D
tsne_lda = tsne_model.fit_transform(df_subset) # doc_topic is document-topic matrix from LDA or GuidedLDA 

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 9958 samples in 0.001s...
[t-SNE] Computed neighbors for 9958 samples in 2.765s...
[t-SNE] Computed conditional probabilities for sample 1000 / 9958
[t-SNE] Computed conditional probabilities for sample 2000 / 9958
[t-SNE] Computed conditional probabilities for sample 3000 / 9958
[t-SNE] Computed conditional probabilities for sample 4000 / 9958
[t-SNE] Computed conditional probabilities for sample 5000 / 9958
[t-SNE] Computed conditional probabilities for sample 6000 / 9958
[t-SNE] Computed conditional probabilities for sample 7000 / 9958
[t-SNE] Computed conditional probabilities for sample 8000 / 9958
[t-SNE] Computed conditional probabilities for sample 9000 / 9958
[t-SNE] Computed conditional probabilities for sample 9958 / 9958
[t-SNE] Mean sigma: 0.000000
[t-SNE] KL divergence after 250 iterations with early exaggeration: 89.805679
[t-SNE] KL divergence after 1000 iterations: 2.090766


In [43]:
from sklearn.manifold import TSNE
from bokeh.plotting import figure, output_file, show
from bokeh.models import Label
from bokeh.io import output_notebook

import matplotlib.colors as mcolors

# Plot the Topic Clusters using Bokeh
output_notebook()
n_topics = 50
mycolors = np.array([color for name, color in mcolors.TABLEAU_COLORS.items()])
plot = figure(title="t-SNE Clustering of {} LDA Topics".format(n_topics), 
              plot_width=400, plot_height=400)
#plot.scatter(x=tsne_lda[:,0], y=tsne_lda[:,1], color=mycolors[topic_num])
plot.scatter(x=tsne_lda[:,0], y=tsne_lda[:,1], color=mycolors)
show(plot)

Loading BokehJS ...